In [1]:
from datetime import datetime, timedelta
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import os
os.environ["DGLBACKEND"] = "pytorch"
import dgl
import dgl.data
import networkx as nx
import hypernetx as hnx
import matplotlib.pyplot as plt
from torch_geometric.nn import RGCNConv
from collections import defaultdict
import warnings

warnings.filterwarnings("ignore", category=FutureWarning)

In [2]:
# Load ICEWS data
icews_data = pd.read_csv('D:\\personal-Shreyas\\AIRS\\data\\raw_data\\rawdat\\IND\\quadruple_idx.txt',sep="\t",names = ["src", "rel", "tgt", "date"])

In [3]:
def get_top_corr_events(data):
    grouped_data = data.groupby(by=["date"])[["src", "tgt", "rel"]].apply(lambda x: x).droplevel(1)
    grouped_data = grouped_data.reset_index()  
    merged = pd.merge(grouped_data, grouped_data, left_on=["src", "tgt", "date"], right_on=["tgt", "src", "date"])
    inverse_rule_mappings = defaultdict(dict)
    most_related_events = defaultdict(list)
    for i in range(len(merged)):
        if merged.rel_x[i] != merged.rel_y[i]:  # Avoid self-mappings (same relations)
            inverse_rule_mappings[merged.rel_x[i]][merged.rel_y[i]] = inverse_rule_mappings[merged.rel_x[i]].get(merged.rel_y[i], 0) + 1
    for relation, mappings in inverse_rule_mappings.items():
        sorted_mappings = sorted(mappings.items(), key=lambda x: x[1], reverse=True)
        for events in sorted_mappings[:3]:
            most_related_events[relation].append(events[0])
    
    return most_related_events

In [4]:
icews_quadruple = pd.read_csv('D:\personal-Shreyas\AIRS\data\IND_data_quintuples\quadruple.csv',names = ["src", "rel", "tgt", "date"])
icews_quadruple.reset_index(drop=True, inplace=True)
icews_quadruple.drop(icews_quadruple.index[0],inplace=True)
icews_quadruple.head()

<>:1: DeprecationWarning: invalid escape sequence \p
<>:1: DeprecationWarning: invalid escape sequence \p
C:\Users\desai\AppData\Local\Temp\ipykernel_19332\3282607156.py:1: DeprecationWarning: invalid escape sequence \p
  icews_quadruple = pd.read_csv('D:\personal-Shreyas\AIRS\data\IND_data_quintuples\quadruple.csv',names = ["src", "rel", "tgt", "date"])


src                                  rel  \
1  Citizen (India)  Acknowledge or claim responsibility   
2         Pakistan    Share intelligence or information   
3            India    Share intelligence or information   
4   Police (India)      Impose administrative sanctions   
5  Citizen (India)                               Demand   

                     tgt        date  
1  Special Court (India)  01-01-2010  
2                  India  01-01-2010  
3               Pakistan  01-01-2010  
4        Citizen (India)  01-01-2010  
5     Government (India)  01-01-2010

In [5]:
icews_quadruple[icews_quadruple["date"].astype(str).str.contains("2014")]

src  \
215185  Central Bureau of Investigation   
215186                            India   
215187                       Shinzo Abe   
215188                 Employee (India)   
215189                 Bharatiya Janata   
...                                 ...   
328659                  Citizen (India)   
328660                  Citizen (India)   
328661                 Children (India)   
328662                   Police (India)   
328663                   Police (India)   

                                                rel  \
215185                                  Investigate   
215186                                 Host a visit   
215187                                 Make a visit   
215188                             Reduce relations   
215189                                      Consult   
...                                             ...   
328659                                       Accuse   
328660                                       Accuse   
328661                                       Accuse   
328662                               Make statement   
328663  Arrest, detain, or charge with legal action   

                                    tgt        date  
215185                  Citizen (India)  01-01-2014  
215186                       Shinzo Abe  01-01-2014  
215187                            India  01-01-2014  
215188  Member of the Judiciary (India)  01-01-2014  
215189                   Indian Express  01-01-2014  
...                                 ...         ...  
328659                  Vasundhara Raje  31-12-2014  
328660                      Amrik Singh  31-12-2014  
328661                   Police (India)  31-12-2014  
328662      Central Intelligence Agency  31-12-2014  
328663                  Citizen (India)  31-12-2014  

[113479 rows x 4 columns]

In [6]:
entity_map = {}
relation_map = {}
with open("D:\\personal-Shreyas\\AIRS\\data\\raw_data\\rawdat\\IND\\entity2id.txt",'r',encoding='utf-8') as file:
    for line in file.readlines():
        entity_map[int(line.split("\t")[1].strip())] = line.split("\t")[0]

with open("D:\\personal-Shreyas\\AIRS\\data\\raw_data\\rawdat\\IND\\relation2id.txt",'r',encoding='utf-8') as file:
    for line in file.readlines():
        relation_map[int(line.split("\t")[1].strip())] = line.split("\t")[0]

In [7]:
date_map={}
with open("D:\\personal-Shreyas\\AIRS\\data\\raw_data\\rawdat\\IND\\quadruple.txt", 'r', encoding='utf-8') as file1, \
     open("D:\\personal-Shreyas\\AIRS\\data\\raw_data\\rawdat\\IND\\quadruple_idx.txt", 'r', encoding='utf-8') as file2:
    
    for line1, line2 in zip(file1.readlines(), file2.readlines()):
        # relation_map[int(line.split("\t")[1].strip())] = line.split("\t")[0]
        date_map[int(line2.split("\t")[3].strip())] = line1.split("\t")[3].strip()

In [8]:
corr_events = get_top_corr_events(icews_data)

In [9]:
# left, rel, right = 2754,19,126

In [10]:
# entity_map[left],entity_map[right],relation_map[rel]

In [11]:
# for _, rows in icews_quadruple.iterrows():
#     if rows["tgt"]==right and rows["src"]==left and rows["rel"]==rel:
#         print(entity_map[rows["src"]], entity_map[rows["tgt"]], relation_map[rows["rel"]], rows["date"])

In [12]:
# for _, rows in icews_quadruple.iterrows():
#     if rows["src"]==right and rows["tgt"]!=left and (rows["rel"]==rel or rows["rel"] in corr_events[rel]):
#         print(entity_map[rows["src"]], entity_map[rows["tgt"]], relation_map[rows["rel"]], rows["date"])

In [13]:
# for _, rows in icews_quadruple.iterrows():
#     if rows["tgt"]==left and rows["src"]!=right and (rows["rel"]==rel or rows["rel"] in corr_events[rel]):
#         print(entity_map[rows["src"]], entity_map[rows["tgt"]], relation_map[rows["rel"]], rows["date"])

In [14]:
def construct_graph(src, rel, dst, date):
    src = np.asarray(src, dtype="int64")
    dst = np.asarray(dst, dtype="int64")
    rel = np.asarray(rel, dtype="int64")
    date = np.asarray(date, dtype="int64")
    print(src, rel, dst, date)
    uniq_v = np.unique((src, dst))
    print(uniq_v)
    g = dgl.graph((len(src),len(dst)))
    # g.add_nodes(len(uniq_v))

    # g.add_edges(src, dst) # array list
    g.edata['type'] = torch.LongTensor(rel)
    g.edata['date'] = torch.LongTensor(date)
    g.ids = {}
    idx = 0
    for id in uniq_v:
        g.ids[id] = idx
        idx += 1
    print(g)
    return g

In [15]:
def plot_graph(graph):
    options = {
        'node_color': 'black',
        'node_size': 50,
        'width': 1,
    }
    G = dgl.to_networkx(graph)
    plt.figure(figsize=[15,7])
    nx.draw(G, **options)
    plt.show()

In [16]:
def construct_graph_for_facts(fact):
    left, rel, right, date = fact
    print(entity_map[left],entity_map[right],relation_map[rel])
    row_graph={}
    key = (left, rel, right, date)
    fact_date = datetime.strptime(date_map[fact[3]], "%Y-%m-%d")  # Adjust the format as necessary
    one_month_ago = fact_date - timedelta(days=30)
    one_month_after = fact_date + timedelta(days=30)
    for _, rows in icews_data.iterrows():
        row_date = datetime.strptime(date_map[rows.date], "%Y-%m-%d") 
        if row_date < one_month_ago or row_date > one_month_after:
            continue

        if key not in row_graph:
            row_graph[key] = {"EXISTING": [], "LEFT": [], "RIGHT": []}
        if rows["tgt"] == right and rows["src"] == left and rows["rel"] == rel :
            row_graph[key]["EXISTING"].append(
                (entity_map[rows.src], relation_map[rows.rel], entity_map[rows.tgt], rows.date)
            )
            # hyper_graph[date][rel] = (left, right)
        
        if rows["src"] == right and rows["tgt"] != left and (rows["rel"] == rel or rows["rel"] in corr_events[rel]):
            row_graph[key]["RIGHT"].append(
                (entity_map[rows.src], relation_map[rows.rel], entity_map[rows.tgt], rows.date)
            )
            # hyper_graph[date][rel] = (left, right)
    
        if rows["tgt"] == left and rows["src"] != right and (rows["rel"] == rel or rows["rel"] in corr_events[rel]):
            row_graph[key]["LEFT"].append(
                (entity_map[rows.src], relation_map[rows.rel], entity_map[rows.tgt], rows.date)
            )
            # hyper_graph[date][rel] = (left, right)

    # rowrow_graphs.get("EXISTING")
    # print("DONE\n",src, relation, tgt, date)
    # print(graph)
    # plot_graph(graph)
    return row_graph

In [17]:
# construct_graph_for_facts([2754,19,126, 123])

In [18]:
row_graphs = []
for _, rows in icews_data.head(1000).iterrows():
    key = [rows.src,rows.rel,rows.tgt,rows.date]
    row_graph= construct_graph_for_facts([rows.src,rows.rel,rows.tgt,rows.date])
    row_graphs.append(row_graph)

Citizen (India) Special Court (India) Acknowledge or claim responsibility
Pakistan India Share intelligence or information
India Pakistan Share intelligence or information
Police (India) Citizen (India) Impose administrative sanctions
Citizen (India) Government (India) Demand
Citizen (India) Samajwadi Janata Party Express intent to meet or negotiate
M.S. Yadav Citizen (India) Demand diplomatic cooperation (such as policy support)
M.S. Yadav Employee (India) Make statement
M.S. Yadav Children (India) Demand
Palaniappan Chidambaram Government (India) Criticize or denounce
United Kingdom India Make statement
Canada India Make statement
Australia India Make statement
Police (India) Student (India) Make statement
Pranab Mukherjee India Make statement
India Pakistan Share intelligence or information
Kangleipak Communist Party Business (India) Abduct, hijack, or take hostage
Police (India) Militant (India) Use conventional military force
India Pakistan Share intelligence or information
Pakist

KeyboardInterrupt: 

In [19]:
hyper_graph = {}
for row in row_graphs:
    for key, value in row.items():
        for value_keys, value_values in value.items():
            for facts in value_values:
                if facts[3] not in hyper_graph:
                    hyper_graph[facts[3]] = {}
                if facts[1] not in  hyper_graph[facts[3]]:
                    hyper_graph[facts[3]][facts[1]] = [[],[]]
                hyper_graph[facts[3]][facts[1]][0].append(facts[0])
                hyper_graph[facts[3]][facts[1]][1].append(facts[2])
for fact_date in hyper_graph:
    for rel in hyper_graph[fact_date]:
        hyper_graph[fact_date][rel] = [tuple(set(inner_list)) for inner_list in hyper_graph[fact_date][rel]]

In [20]:
hyper_graph = {}
for row in row_graphs:
    for key, value in row.items():
        for value_keys, value_values in value.items():
            for facts in value_values:
                # if facts[3] not in hyper_graph:
                #     hyper_graph[facts[3]] = {}
                if facts[1] not in  hyper_graph:
                    hyper_graph[facts[1]] = [[],[]]
                hyper_graph[facts[1]][0].append(facts[0])
                hyper_graph[facts[1]][1].append(facts[2])
# for fact_date in hyper_graph:
for rel in hyper_graph:
    hyper_graph[rel] = [tuple(set(inner_list)) for inner_list in hyper_graph[rel]]

In [21]:
# for key, value in hyper_graph.items():
H = hnx.Hypergraph(hyper_graph)
## HNX has a built in draw function - more information may be found in tutorial Basic 2
plt.subplots(figsize=(100,100))
hnx.draw(H)
plt.savefig((f'./hypergraphs/full month_hg.png'))

C:\Users\desai\anaconda3\envs\cuda_test\lib\site-packages\hypernetx\classes\entityset.py:150: DeprecationWarning: misc_props_col and misc_cell_props_col will be deprecated; all public references to these arguments will be removed in a future release.
  warnings.warn(
C:\Users\desai\anaconda3\envs\cuda_test\lib\site-packages\hypernetx\classes\hypergraph.py:563: FutureWarning: This method or function will be deprecated in a future release. Public references to this method or function will be removed from the Hypergraph API in a future release.
  self._nodes = self.E.restrict_to_levels([1])
C:\Users\desai\anaconda3\envs\cuda_test\lib\site-packages\hypernetx\classes\entityset.py:150: DeprecationWarning: misc_props_col and misc_cell_props_col will be deprecated; all public references to these arguments will be removed in a future release.
  warnings.warn(
C:\Users\desai\anaconda3\envs\cuda_test\lib\site-packages\hypernetx\classes\entityset.py:1494: RuntimeWarning: The values in the array ar